# Importy bibliotek

In [2]:
import pandas as pd
import numpy as np

from wordcloud import WordCloud

from ydata_profiling import ProfileReport

from collections import Counter

import matplotlib
matplotlib.use('TkAgg')	# używam backendu z GUI - potrzebne do wyświetlania wykresów lokalnie (bez tego plt.show() nie działa mi lokalnie)
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize
from matplotlib.cm import ScalarMappable, get_cmap

import plotly.graph_objects as go
import seaborn as sns

from langchain.chat_models import ChatOpenAI
from langchain.prompts import (
    ChatPromptTemplate,
    SystemMessagePromptTemplate,
    HumanMessagePromptTemplate
)

#potrzebne do kodu, który będzie tłumaczył:
from langchain_openai import ChatOpenAI				
from langchain.output_parsers import CommaSeparatedListOutputParser

# Ustawienie opcji wyświetlania

In [26]:
pd.set_option('display.max_columns', None)	#aby wyświetlane były wszystkie kolumny
pd.set_option('display.max_colwidth', None)	#aby była wyświetlana cała zawartość tekstu, a nie była obcinana, gdy jest długa

# Wczytanie danych

In [3]:
df = pd.read_json("C:\\Users\\justy\\Documents\\Projekt\\03_projekt_dane_wyciągniete_NER_i_listy_z_opisow.json")  #wczytanie danych
df.tail(5)	#sprawdzam 5 ostatnich wierszy

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
52                                                                                                                                                         [left ovarian endometrial cyst]   
53                                                                                                                         [adenomyosis, ovary, endometriosis, uterus, adnexa, intestines]   
54                                                                                                                 [adenomyosis, tumor, rectum, umbilicus, endometriosis, adhesions, cyst]   
55  [left parametrium, tumor, sacrouterine ligament, endometriosis - stage 4, left ovarian cyst, endometriosis, diaphragm, sigmoid colon, ovarian cyst, intra-abdominal adhesions, tumors]   
56                                                                                                                     [superficial, ovary, foci, endometriosis, endometrial cyst, pelvis]   

                                                                                                                                                                                                  Wyodrebnione_rozpoznania_pooperacyjne  \
52                                                                                                                                                                                                        Left ovarian endometrial cyst   
53                                                                                                                                                                                                           Endometriosis, Adenomyosis   
54                                                                               Endometriosis stage IV, adenomyosis, tumor of the rectum, tumor of the small intestine, tumor of the large intestine, adhesions, cyst in the umbilicus   
55  Deep infiltrating endometriosis of the left parametrium, intra-abdominal adhesions, advanced endometriosis - stage 4, left ovarian cyst, adhesion of the sigmoid colon, tumor on the sacrouterine ligament, tumors on the diaphragm   
56                                                                                   Endometrial cyst on left ovary, Superficial endometriosis on right ovary, Endometriosis in the lesser pelvis, Trace of free fluid in Douglas pouch   

                                                                                                                                                                                                Tlumaczenie_Ang_Rozpoznanie_pooperacyjne  \
52                                                                                                                                                                                                         Left ovarian endometrial cyst   
53                                                                                  Endometriosis and adenomyosis.  \nLaparotomy, removal of the body of the uterus along with the adnexa and the left ovary. Release of the intestines.   
54                                                                            Endometriosis stage IV with deep infiltration, adenomyosis, tumor of the rectum, tumor of the small and large intestine, adhesions, cyst in the umbilicus.   
55  Deep infiltrating endometriosis of the left parametrium, intra-abdominal adhesions, advanced endometriosis - stage 4, left ovarian cyst, adhesion of the sigmoid colon, tumor on the sacrouterine ligament, tumors on the diaphragm.   
56        Left ovary with a hypoechoic lesion characteristic of an endometrial cyst measuring 40mm. Right ovary with foci of superficial endometriosis. Foci of endometriosis in the lesser pelvis. Douglas pouch - trace of free fluid.   

                                                                 Tlumaczenie_Ang_Zakres_operacji_entities  \
52                                                         

# Odczyt klucza API

In [ ]:
api_key = open("C:\\...\\api openai key.txt").read()	# w miejsce ... ma być lokalizacja
model_1 = ChatOpenAI(model='gpt-4o', temperature=0.0, openai_api_key=api_key)

# Definicje funkcji

In [5]:
# Ekstrakcja unikalnych symptomów, diagnoz, metod itd.
def extract_unique_values(df, column_name):
    return (
        df[column_name]
        .dropna()  # Usunięcie NaN
        .str.split(",")  # Rozdzielenie tekstów na listy przy przecinkach
        .explode()  # Rozbicie list na pojedyncze wiersze
        .str.strip()  # Usunięcie zbędnych spacji
        .drop_duplicates()  # Usunięcie duplikatów
    )

In [6]:
# Funkcja do generowania reprezentatywnego terminu
def get_representative_term(term):
    try:
        prompt = chat_template.format_prompt(term=term)
        response_list = []
        for chunk in model_1.stream(prompt.to_messages()):
            response_list.append(chunk.content)
        # Łączenie fragmentów odpowiedzi w jedno
        response_text = ''.join(response_list).replace('\n', ' ').strip()
        return response_text
    except Exception as e:
        print(f"Error generating representative term for '{term}': {e}")
        return term  # Zwróć oryginalny termin w przypadku błędu

In [7]:
# Funkcja do tworzenia słownika normalizacji
def create_normalization_dict(terms):
    normalization_dict = {}
    for term in terms:
        if term not in normalization_dict:  # Unikaj duplikatów
            # Generowanie reprezentatywnego terminu
            normalization_dict[term] = get_representative_term(term)
    return normalization_dict

In [8]:
# Uniwersalna funkcja do normalizacji tekstu w kolumnie
def normalize_text_column(text, normalization_dict):
    if not isinstance(text, str):  # Obsługa NaN lub innych typów
        return text
    # Rozdziel tekst na pojedyncze elementy, znormalizuj, a następnie połącz
    znormalizowane = [
        normalization_dict.get(symptom.strip().lower(), symptom.strip().lower()) 
        for symptom in text.split(",")
    ]
    return ", ".join(znormalizowane)


In [9]:
# Funkcja usuwająca zduplikowane wyrażenia z tekstu
def remove_duplicate_phrases(text):
    if isinstance(text, str):  # Sprawdzenie, czy wartość jest ciągiem znaków
        phrases = [phrase.strip() for phrase in text.split(',')]  # Podział na wyrażenia i usunięcie zbędnych spacji
        unique_phrases = list(dict.fromkeys(phrases))  # Usunięcie duplikatów zachowując kolejność
        return ', '.join(unique_phrases)
    return text

# NLP
We wcześniejszym kroku zostały w formie list wyciągnięte najważniejsze informacje z opisów od osób wypełniających ankiety.
Model LLM nie wyciąga informacji idealnie, na przykład dwie te same dolegliwości mogą mieć różne brzmienie, np. "Lower abdominal pain" albo "pain in the lower abdomen".
Do rozwiązania tego problemu spróbuję użyć technik NLP

## Dla kolumny "Wyodrebnione_dolegliwosci":

In [10]:
# Ekstrakcja unikalnych symptomów, używam wcześniej utworzonej funkcji extract_unique_values
unique_symptoms = extract_unique_values(df, "Wyodrebnione_dolegliwosci")

# Konwersja do listy
unique_symptoms_list = unique_symptoms.tolist()

In [11]:
# Wyświetlenie wyników
unique_symptoms_list

['lower back pain',
 'urinary system issues',
 'decreased urine pressure',
 'pain in ureter',
 'pain in kidney areas',
 'sharp pain',
 'cold sweats',
 'constipation',
 'pain on the left side under the rib',
 'lower abdominal pain',
 'pain on the left side of the pelvis',
 'pain in the groin',
 'pain in the lower abdomen',
 'frequent and painful urination',
 'sensation of incomplete bladder emptying',
 'Difficulty urinating',
 'narrow stream',
 'straining to empty bladder',
 'urinary incontinence',
 'abdominal pain',
 'intestinal pain',
 'Adhesion pain',
 'frequent discomfort',
 'No symptoms provided',
 'Diarrhea',
 'loss of bladder sensation',
 'pulling sensation in lower abdomen',
 'Radiating pain to the left leg',
 'pain in both buttocks',
 'pain in the left sacrouterine ligament',
 'breast pain',
 'increased sweating',
 'back pain',
 'abdominal hypersensitivity',
 'lack of sensation in the vagina',
 'bowel movement issues',
 'Periodic pain in the ovaries',
 'right leg pain',
 'intes

In [12]:
# Szablony promptów dla wyodrębniania synonimów
system_template = """
You are an assistant that helps group medical terms and conditions into a single representative term. For example:
- "Lower abdominal pain" and "Pain in the lower abdomen" → "Abdominal pain".
- "Urinary issues" and "Bladder problems" → "Urinary issues".
Provide the most representative term for the input.
"""

human_template = """
What is the most representative term for the following condition: "{term}"?
"""

system_prompt = SystemMessagePromptTemplate.from_template(system_template)
human_prompt = HumanMessagePromptTemplate.from_template(human_template)
chat_template = ChatPromptTemplate.from_messages([system_prompt, human_prompt])

In [13]:
# Lista unikalnych symptomów
unique_symptoms = unique_symptoms_list

# Generowanie słownika normalizacji
normalization_dict = create_normalization_dict(unique_symptoms)

In [14]:
# Zamiana kluczy i wartości na małe litery
znormalizowane_dict = {key.lower(): value.lower() for key, value in normalization_dict.items()}

# Wyświetlenie wyniku
znormalizowane_dict

{'lower back pain': 'back pain',
 'urinary system issues': 'urinary issues',
 'decreased urine pressure': 'urinary issues',
 'pain in ureter': 'ureteral pain',
 'pain in kidney areas': 'kidney pain',
 'sharp pain': 'pain',
 'cold sweats': 'diaphoresis',
 'constipation': 'gastrointestinal issue',
 'pain on the left side under the rib': 'the most representative term for "pain on the left side under the rib" is "flank pain".',
 'lower abdominal pain': 'abdominal pain',
 'pain on the left side of the pelvis': 'pelvic pain',
 'pain in the groin': 'groin pain',
 'pain in the lower abdomen': 'abdominal pain',
 'frequent and painful urination': 'urinary issues',
 'sensation of incomplete bladder emptying': 'urinary retention',
 'difficulty urinating': 'urinary issues',
 'narrow stream': 'urinary hesitancy',
 'straining to empty bladder': 'urinary retention',
 'urinary incontinence': 'urinary issues',
 'abdominal pain': 'the most representative term for "abdominal pain" is "abdominal pain".',
 

Po przejrzeniu słownika normalizacji widzę, że wyniki są w miarę dobre, ale w niektórych przypadkach wyniki są nieporządane tzn. zamiast krótkich synonimów, jest opis. Dodatkowo w niektórych przypadkach model niepotrzebnie próbował wprowadzić synonim (np. dla 'back pain': 'musculoskeletal pain' powinien zostać po prostu 'back pain'). W związku z tym część dolegliwości ze słownika poprawię ręcznie. Niestety LLM nie poradził sobie wystarczająco dobrze z zadaniem.

In [ ]:
# Ręczna poprawa słownika normalizacji dla kolumny z dolegliwościami:
normalization_dict = {
'lower back pain': 'back pain',
 'urinary system issues': 'urinary issues',
 'decreased urine pressure': 'urinary retention',
 'pain in ureter': 'ureteral pain',
 'pain in kidney areas': 'kidney pain',
 'sharp pain': 'sharp pain',
 'cold sweats': 'cold sweats',
 'constipation': 'constipation',
 'pain on the left side under the rib': 'left-sided abdominal pain',
 'lower abdominal pain': 'abdominal pain',
 'pain on the left side of the pelvis': 'left-sided abdominal pain',
 'pain in the groin': 'groin pain',
 'pain in the lower abdomen': 'abdominal pain',
 'frequent and painful urination': 'urinary issues',
 'sensation of incomplete bladder emptying': 'urinary retention',
 'difficulty urinating': 'urinary issues',
 'narrow stream': 'urinary issues',
 'straining to empty bladder': 'urinary retention',
 'urinary incontinence': 'urinary issues',
 'abdominal pain': 'abdominal pain',
 'intestinal pain': 'abdominal pain',
 'adhesion pain': 'adhesions',
 'frequent discomfort': 'general discomfort',
 'no symptoms provided': 'no symptoms provided',
 'diarrhea': 'diarrhea',
 'loss of bladder sensation': 'urinary issues',
 'pulling sensation in lower abdomen': '"abdominal discomfort"',
 'radiating pain to the left leg': 'sciatica',
 'pain in both buttocks': 'buttock pain',
 'pain in the left sacrouterine ligament': 'pelvic pain',
 'breast pain': 'mastalgia',
 'increased sweating': 'hyperhidrosis',
 'back pain': 'back pain',
 'abdominal hypersensitivity': 'abdominal tenderness',
 'lack of sensation in the vagina': 'vaginal numbness',
 'bowel movement issues': 'constipation',
 'periodic pain in the ovaries': 'ovarian pain',
 'right leg pain': 'leg pain',
 'intestinal cramps': 'abdominal pain',
 'pain on the right side of the ribs': '"rib pain"',
 'chest pain': 'chest pain',
 'right shoulder pain': 'shoulder pain',
 'frequent urination': 'urinary frequency',
 'bladder pain': 'bladder pain',
 'pain on the right side of the ovary': 'ovarian pain',
 'cough': 'respiratory symptom',
 'hemoptysis': 'hemoptysis',
 'painful urination': 'dysuria',
 'abdominal tenderness': 'abdominal tenderness',
 'difficulty with defecation': 'constipation',
 'pain on left side': 'left-sided abdominal pain',
 'visible swelling': 'swelling',
 'fatigue': 'fatigue',
 'pain in the left ovary area': 'left-sided abdominal pain',
 'severe pain in the lumbar region': 'back pain',
 'loss of sensation': 'numbness',
 'persistent pain': 'chronic pain',
 'radiating pain': 'nerve pain',
 'bowel problems': 'gastrointestinal issues',
 'pain in the left lower abdomen': 'left-sided abdominal pain',
 'menstrual disorders': 'menstrual disorders',
 'rapid progression of deep infiltrating endometriosis': 'rapid progression of deep infiltrating endometriosis',
 'burning pain': 'neuropathic pain',
 'lower abdomen pain': 'abdominal pain',
 'pelvic pain': 'pelvic pain',
 'sharp pains in ovarian area': '"ovarian pain"',
 'pain radiating to pubic symphysis': 'pelvic pain',
 'feeling of incomplete bowel evacuation': 'constipation',
 'too frequent urge to urinate': 'urinary frequency',
 'rare need to urinate': 'urinary retention',
 'lack of sensation of a full bladder': 'urinary issues',
 'pain in the lumbar region': 'back pain',
 'painful menstruation': 'dysmenorrhea',
 'pressure on the bladder': 'urinary issues',
 'chronic fatigue': 'chronic fatigue',
 'tremors': 'tremors',
 'depression': 'depression',
 'incomplete bowel evacuation': 'constipation',
 'nausea': 'nausea',
 'mood swings': 'mood swings',
 'hot flashes': 'menopausal symptoms',
 'chronic anxiety': 'anxiety',
 'severe intestinal pain': 'abdominal pain',
 'sensation of narrowing': 'constipation',
 'digestive issues': '"gastrointestinal issues"',
 'reflux': 'reflux',
 'shortness of breath': 'respiratory distress',
 'pain in thoracic spine': 'back pain',
 'pain in lumbar spine': 'back pain',
 'pain in neck': 'neck pain',
 'pain on the left side': 'left-sided abdominal pain',
 'feeling of incomplete bladder emptying': 'urinary retention',
 'burning pain in the lower abdomen': 'abdominal pain'
}

In [16]:
# Zastosowanie funkcji normalize_text_column do kolumny "Wyodrebnione_dolegliwosci"
df["Wyodrebnione_dolegliwosci_znormalizowane"] = df["Wyodrebnione_dolegliwosci"].apply(normalize_text_column, args=(normalization_dict,))

# Przeniesienie kolumn z wyestrahowanymi informacjami przed ich odpowiadającą kolumną
cols = list(df.columns)
cols.insert(cols.index('Tlumaczenie_Ang_Rodzaje_dolegliwosci'), cols.pop(cols.index('Wyodrebnione_dolegliwosci_znormalizowane')))


# Przestawienie DataFrame według zaktualizowanej listy kolumn:
df = df[cols]


In [17]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                                                                                                                                                                                                                                                                                                                               Tlumaczenie_Ang_Rozpoznanie_pooperacyjne  \
0  Condition after 4 surgical procedures. Intra-abdominal adhesions. Adenomyosis of the uterine body. Deep infiltrating endometriosis of the left parametrium. In the area of the left ureter and the left uterosacral ligament. Right parametr

Po normalizacji zastosowanej do kolumny z dolegliwościami widać, że czasami powtarzają się dolegliwości. W następnym kroku zostaną usunięte powtórzenia.

In [18]:
# Usunięcie powtórzeń w komórkach kolumny "Wyodrebnione_dolegliwosci_znormalizowane"
# Zastosowanie funkcji do kolumny 'Wyodrebnione_dolegliwosci_znormalizowanewane'
df['Wyodrebnione_dolegliwosci_znormalizowane'] = df['Wyodrebnione_dolegliwosci_znormalizowane'].apply(remove_duplicate_phrases)


In [19]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                                                                                                                                                                                                                                                                                                                               Tlumaczenie_Ang_Rozpoznanie_pooperacyjne  \
0  Condition after 4 surgical procedures. Intra-abdominal adhesions. Adenomyosis of the uterine body. Deep infiltrating endometriosis of the left parametrium. In the area of the left ureter and the left uterosacral ligament. Right parametr

Normalizacja tekstów z dolegliwościami wydaje się mieć bardzo dobre rezultaty. Podobne procesy zostaną przeprowadzone na pozostałych kolumnach z opisami od respondentek. Pozostałe kolumny to:
- Wyodrebnione_rozpoznania_pooperacyjne
- Wyodrebnione_zakres_operacji
- Wyodrebnione_dodatkowe_metody
- Wyodrebnione_dodatkowe_choroby_i_zaburzenia

## Grupowanie tekstów z diagnozami (kolumna Wyodrebnione_rozpoznania_pooperacyjne)

In [20]:
# Ekstrakcja unikalnych wyrażeń dla diagnoz pooperacyjnych, używam wcześniej utworzonej funkcji extract_unique_values
unique_postoperative_diagnoses = extract_unique_values(df, "Wyodrebnione_rozpoznania_pooperacyjne")

# Konwersja do listy
unique_postoperative_diagnoses_list = unique_postoperative_diagnoses.tolist()

In [21]:
unique_postoperative_diagnoses_list

['Intra-abdominal adhesions',
 'Adenomyosis of the uterine body',
 'Deep infiltrating endometriosis of the left parametrium',
 'Right parametric endometriosis',
 'Endometrial tumor at the cervix',
 'Endometriosis of the left adnexa',
 'Pain localized in other parts of the lower abdomen',
 'peritoneal diseases',
 'endometriosis',
 'Stage IV endometriosis',
 'Adhesions',
 'Frozen pelvis',
 'Endometrial mass on the ovary',
 'Masses in the rectum',
 'Bowel fused with the uterus',
 'Bowel adhered to the peritoneum',
 'Ovaries retracted behind the uterus',
 'Ovaries fused with the uterus',
 'Ovaries fused with the bowel',
 'Bladder displaced',
 'Bladder tethered by adhesions',
 'Adhesions on the parametrium',
 'Adhesions on the ligaments',
 'Advanced adenomyosis',
 'left parametric endometriosis',
 'right parametric endometriosis',
 'ovarian endometriosis',
 'intra-abdominal adhesions',
 'Intra- and extra-peritoneal adhesions',
 'right ovarian cysts',
 'deeply infiltrating endometriosis of t

W kolejnym kroku pogrupuję diagnozy w celu zmniejszenia różnorodności i ułatwienia późniejszej analizy. Ręcznie wpiszę w prompt jak mają być pogrupowane. W pierwszej kolejności wypróbowałam grupowanie wykorzystując model BERT (do generowania kontekstualnych embeddingów, które uwzględniają znaczenie słów) i algorytm klastrowania k-means do klastrowania embeddingów, ale nie uzyskałam satysfakcjonujących rezultatów. Znacznie lepszy rezultat daje użycie LLM, dla którego kod jest wpisany poniżej. Szablon promptu ma inną treść niż dla symptomów, w przeciwnym wypadku model nie zrozumiałby prawidłowo jak pogrupować medyczne terminy.

In [22]:
# Szablony promptów zmodyfikowane w stosunku do wcześniejszych do celów grupowania diagnoz
system_template = """
You are an assistant that helps group medical terms and diagnoses into a single representative term. For example:
- "Lower abdominal pain" and "Pain in the lower abdomen" → "Abdominal pain".
- "Urinary issues" and "Bladder problems" → "Urinary issues".
- "Deep infiltrating endometriosis of the left parametrium' → "Deep infiltrating endometriosis (DIE)".
- "Endometrial mass on the ovary" and "Endometrial cyst on left ovary" → "ovarian endometriosis".
- "frozen pelvis" → "Adhesions"
Provide the most representative term for the input.
"""

human_template = """
What is the most representative term for the following diagnoses: "{term}"?
"""

system_prompt = SystemMessagePromptTemplate.from_template(system_template)
human_prompt = HumanMessagePromptTemplate.from_template(human_template)
chat_template = ChatPromptTemplate.from_messages([system_prompt, human_prompt])

# Funkcje takie same jak dla symptomów, są wyżej

# Lista unikalnych diagnoz
unique_diagnoses = unique_postoperative_diagnoses_list

# Generowanie słownika normalizacji
normalization_dict_diagnoses = create_normalization_dict(unique_diagnoses)

# Zamiana kluczy i wartości na małe litery
znormalizowane_dict_diagnoses = {key.lower(): value.lower() for key, value in normalization_dict_diagnoses.items()}


In [23]:
# Wyświetlenie wyniku
znormalizowane_dict_diagnoses

{'intra-abdominal adhesions': 'adhesions',
 'adenomyosis of the uterine body': 'adenomyosis',
 'deep infiltrating endometriosis of the left parametrium': 'deep infiltrating endometriosis (die)',
 'right parametric endometriosis': 'deep infiltrating endometriosis (die)',
 'endometrial tumor at the cervix': 'cervical endometriosis',
 'endometriosis of the left adnexa': '"adnexal endometriosis"',
 'pain localized in other parts of the lower abdomen': 'abdominal pain',
 'peritoneal diseases': 'peritoneal disease',
 'endometriosis': 'endometriosis',
 'stage iv endometriosis': '"advanced endometriosis"',
 'adhesions': 'adhesions',
 'frozen pelvis': 'adhesions',
 'endometrial mass on the ovary': 'ovarian endometriosis',
 'masses in the rectum': 'rectal masses',
 'bowel fused with the uterus': 'adhesions',
 'bowel adhered to the peritoneum': 'adhesions',
 'ovaries retracted behind the uterus': '"ovarian adhesions"',
 'ovaries fused with the uterus': 'adhesions',
 'ovaries fused with the bowel'

In [24]:
# Zastosowanie wcześniej utworzonej funkcji normalize_text_column do kolumny z diagnozami: "Wyodrebnione_rozpoznania_pooperacyjne"
df["Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane"] = df["Wyodrebnione_rozpoznania_pooperacyjne"].apply(normalize_text_column, args=(znormalizowane_dict_diagnoses,))

# Przeniesienie kolumn z wyestrahowanymi informacjami przed ich odpowiadającą kolumną
cols = list(df.columns)
cols.insert(cols.index('Tlumaczenie_Ang_Rozpoznanie_pooperacyjne'), cols.pop(cols.index('Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane')))

# Przestawienie DataFrame według zaktualizowanej listy kolumn:
df = df[cols]


In [25]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0                                                             adhesions, adenomyosis, deep infiltrating endometriosis (die), deep infiltrating endometriosis (die), cervical endometriosis, "adnexal endometriosis"   
1                                                                                                                                                                 abdominal pain, peritoneal disease, endome

In [ ]:
#Przeglądając dataframe zauważyłam, że w niektóre diagnozy są w cudzysłowiu. Usunę znaki cudzysłowia. Poza tym wyniki wydają się być prawidłowe.

# Usunięcie cudzysłowów
df['Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'] = df['Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'].str.replace('"', '', regex=False)

# Usunięcie powtórzeń w komórkach kolumny "Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane"
# Zastosowanie wcześniej utworzonej funkcji (przy symptomach): remove_duplicate_phrases, do kolumny 'Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'
df['Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'] = df['Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'].apply(remove_duplicate_phrases)


In [27]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                               Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0      adhesions, adenomyosis, deep infiltrating endometriosis (die), cervical endometriosis, adnexal endometriosis   
1                                                                 abdominal pain, peritoneal disease, endometriosis   
2  advanced endometriosis, adhesions, ovarian endometriosis, rectal masses, ovarian adhesions, bladder displacement   
3                              adenomyosis, deep infiltrating endometriosis (die), ovarian endometriosis, adhesions   
4          adhesions, ovarian cysts, de

## Te same kroki co wyżej zostaną podjęte do kolejne kolumny: "Wyodrebnione_zakres_operacji"

In [28]:
# Ekstrakcja unikalnych wyrażeń dla kolumny z opisami co wykonano podczas operacji, używam wcześniej utworzonej funkcji extract_unique_values
unique_surgery = extract_unique_values(df, "Wyodrebnione_zakres_operacji")

# Konwersja do listy
unique_surgery_list = unique_surgery.tolist()

In [29]:
# Szablony promptów zmodyfikowane w stosunku do wcześniejszych do celów grupowania wyrażeń związanych z wykonanymi czynnościami podczas operacji
system_template = """
You are an assistant that helps group surgical procedure descriptions into specific, detailed representative terms. For example:
- "Release of adhesions", "release from intestinal adhesions" and "laparoscopic adhesiolysis" → "Adhesiolysis"
- "Removal of endometriosis from the left parametrium" and "removal of endometriosis from the left pelvic wall" → "Excision of endometriosis from the left pelvic region"
- "Laparoscopic hysterectomy" and "hysterectomy" → "Hysterectomy"
- "Anti-adhesion gel" and "adhesion prevention" → "Adhesion prevention"

Generate only the most representative and detailed term for the input descriptions without adding a period (".") or other extra punctuation at the end.
"""

# Zmieniony human_template, aby pozostał zgodny z system_template
human_template = """
What is the most representative term for the surgical procedure: "{term}"?
"""

system_prompt = SystemMessagePromptTemplate.from_template(system_template)
human_prompt = HumanMessagePromptTemplate.from_template(human_template)
chat_template = ChatPromptTemplate.from_messages([system_prompt, human_prompt])

# Funkcje takie same jak dla symptomów, są wyżej

# Lista unikalnych diagnoz
unique_surgery = unique_surgery_list

# Generowanie słownika normalizacji
normalization_dict_surgery = create_normalization_dict(unique_surgery)

# Zamiana kluczy i wartości na małe litery
znormalizowane_dict_surgery = {key.lower(): value.lower() for key, value in normalization_dict_surgery.items()}


In [30]:
# Wyświetlenie wyniku
znormalizowane_dict_surgery

{'release of adhesions': 'adhesiolysis',
 'removal of endometriosis from the left and right parametrium': 'excision of endometriosis from the bilateral parametrium',
 'laparoscopic hysterectomy': 'hysterectomy',
 'adhesion prevention': 'adhesion prevention',
 'drainage of the peritoneal cavity': 'peritoneal cavity drainage',
 'excision of peritoneal tissues': 'excision of peritoneal tissue',
 'removal of the left sacrouterine ligament with a fragment of the peritoneum from the douglas pouch': 'excision of the left sacrouterine ligament and peritoneum from the douglas pouch',
 'removal of the peritoneum from the anterior wall of the abdominal cavity': 'excision of peritoneum from the anterior abdominal wall',
 'release from adhesions': 'adhesiolysis',
 'removal of the left ovary with appendages': 'salpingo-oophorectomy on the left side',
 'excision of endometrial lesions from the right ovary': 'excision of endometriosis from the right ovary',
 'removal of the right appendages': 'salping

In [31]:
# Zastosowanie wcześniej utworzonej funkcji normalize_text_column do kolumny z diagnozami: "Wyodrebnione_zakres_operacji"
df["Wyodrebnione_zakres_operacji_znormalizowane"] = df["Wyodrebnione_zakres_operacji"].apply(normalize_text_column, args=(znormalizowane_dict_surgery,))

# Przeniesienie kolumn z wyestrahowanymi informacjami przed ich odpowiadającą kolumną
cols = list(df.columns)
cols.insert(cols.index('Tlumaczenie_Ang_Zakres_operacji_entities'), cols.pop(cols.index('Wyodrebnione_zakres_operacji_znormalizowane')))

# Przestawienie DataFrame według zaktualizowanej listy kolumn:
df = df[cols]


In [32]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                               Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0      adhesions, adenomyosis, deep infiltrating endometriosis (die), cervical endometriosis, adnexal endometriosis   
1                                                                 abdominal pain, peritoneal disease, endometriosis   
2  advanced endometriosis, adhesions, ovarian endometriosis, rectal masses, ovarian adhesions, bladder displacement   
3                              adenomyosis, deep infiltrating endometriosis (die), ovarian endometriosis, adhesions   
4          adhesions, ovarian cysts, de

In [ ]:
# Usunięcie powtórzeń w komórkach kolumny "Wyodrebnione_zakres_operacji_znormalizowane"
# Zastosowanie wcześniej utworzonej funkcji (przy symptomach): remove_duplicate_phrases
df['Wyodrebnione_zakres_operacji_znormalizowane'] = df['Wyodrebnione_zakres_operacji_znormalizowane'].apply(remove_duplicate_phrases)


In [34]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                               Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0      adhesions, adenomyosis, deep infiltrating endometriosis (die), cervical endometriosis, adnexal endometriosis   
1                                                                 abdominal pain, peritoneal disease, endometriosis   
2  advanced endometriosis, adhesions, ovarian endometriosis, rectal masses, ovarian adhesions, bladder displacement   
3                              adenomyosis, deep infiltrating endometriosis (die), ovarian endometriosis, adhesions   
4          adhesions, ovarian cysts, de

## Kolejny krok: wykonanie powyższych operacji dla kolumny 'Wyodrebnione_dodatkowe_metody'

In [35]:
# Ekstrakcja unikalnych wyrażeń dla kolumny Wyodrebnione_dodatkowe_metody, używam wcześniej utworzonej funkcji extract_unique_values
unique_methods = extract_unique_values(df, "Wyodrebnione_dodatkowe_metody")

# Konwersja do listy
unique_methods_list = unique_methods.tolist()

In [36]:
# Szablony promptów zmodyfikowane w stosunku do wcześniejszych do celów grupowania wyrażeń w kolumne Wyodrebnione_dodatkowe_metody
system_template = """
You are an assistant that helps group alternative methods for managing health conditions into a single representative term. For example:
- "Cognitive behavioral therapy" and "Psychotherapy" → "Psychotherapy"
- "Acupuncture" and "Cupping therapy" → "Acupuncture"
- "Meditation" and "Breathing exercises" → "Meditation"
- "Physiotherapy" and "Massage therapy" → "Physiotherapy"
- "Supplements for health improvement" and "Treatment with supplements" → "Treatment with supplements"

Provide only the most concise and representative term for the input alternative method. Do not include additional descriptions, punctuation, or phrases like "can be grouped under".
"""

# Zmieniony human_template, aby pozostał zgodny z system_template
human_template = """
What is the most representative term for the method for managing health condidions: "{term}"?
"""

system_prompt = SystemMessagePromptTemplate.from_template(system_template)
human_prompt = HumanMessagePromptTemplate.from_template(human_template)
chat_template = ChatPromptTemplate.from_messages([system_prompt, human_prompt])

# Funkcje takie same jak dla symptomów, są wyżej

# Lista unikalnych metod
unique_methods = unique_methods_list

# Generowanie słownika normalizacji
normalization_dict_methods = create_normalization_dict(unique_methods)



In [37]:
# Zamiana kluczy i wartości na małe litery
znormalizowane_dict_methods = {key.lower(): value.lower() for key, value in normalization_dict_methods.items()}

# Wyświetlenie wyniku
znormalizowane_dict_methods

{'psychotherapy': 'psychotherapy',
 'acupuncture': 'acupuncture',
 'yoga': 'yoga',
 'physiotherapy': 'physiotherapy',
 'medical marijuana': 'cannabis therapy',
 'meditation': 'meditation',
 'massage': 'massage therapy',
 'cupping': 'acupuncture',
 'naturopathy': 'naturopathy',
 'treatment with supplements': 'supplements',
 'breathing exercises': 'meditation',
 'self-development books': 'self-help books',
 'slavic gymnastics': 'slavic gymnastics',
 'psychotherapy assistance': 'psychotherapy',
 'meditations': 'meditation',
 'stretching exercises': 'stretching',
 'massages': 'massage therapy',
 'urogynaecological physiotherapy': 'physiotherapy',
 'pilates': 'exercise',
 'ssris': 'antidepressants',
 'consultation with psychiatrists': 'psychotherapy',
 'walking': 'walking',
 'napping': 'sleep therapy',
 'relaxation with asmr': 'asmr',
 'partially following dietitian recommendations': 'dietary management',
 'advice from tim spector': 'dietary guidance',
 'advice from will bulsiewicz': 'nutri

In [38]:
# Zastosowanie wcześniej utworzonej funkcji normalize_text_column do kolumny z diagnozami: "Wyodrebnione_dodatkowe_metody"
df["Wyodrebnione_dodatkowe_metody_znormalizowane"] = df["Wyodrebnione_dodatkowe_metody"].apply(normalize_text_column, args=(znormalizowane_dict_methods,))

# Przeniesienie kolumn z wyestrahowanymi informacjami przed ich odpowiadającą kolumną
cols = list(df.columns)
cols.insert(cols.index('Tlumaczenie_Ang_Jakie_inne_metody'), cols.pop(cols.index('Wyodrebnione_dodatkowe_metody_znormalizowane')))

# Przestawienie DataFrame według zaktualizowanej listy kolumn:
df = df[cols]


In [39]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                               Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0      adhesions, adenomyosis, deep infiltrating endometriosis (die), cervical endometriosis, adnexal endometriosis   
1                                                                 abdominal pain, peritoneal disease, endometriosis   
2  advanced endometriosis, adhesions, ovarian endometriosis, rectal masses, ovarian adhesions, bladder displacement   
3                              adenomyosis, deep infiltrating endometriosis (die), ovarian endometriosis, adhesions   
4          adhesions, ovarian cysts, de

In [ ]:
# Usunięcie powtórzeń w komórkach kolumny "Wyodrebnione_dodatkowe_metodyy_znormalizowane"
# Zastosowanie wcześniej utworzonej funkcji (przy symptomach): remove_duplicate_phrases, do kolumny 'Wyodrebnione_dodatkowe_metody_znormalizowane'
df['Wyodrebnione_dodatkowe_metody_znormalizowane'] = df['Wyodrebnione_dodatkowe_metody_znormalizowane'].apply(remove_duplicate_phrases)


In [41]:
# Wyświetlenie wyniku
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                               Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0      adhesions, adenomyosis, deep infiltrating endometriosis (die), cervical endometriosis, adnexal endometriosis   
1                                                                 abdominal pain, peritoneal disease, endometriosis   
2  advanced endometriosis, adhesions, ovarian endometriosis, rectal masses, ovarian adhesions, bladder displacement   
3                              adenomyosis, deep infiltrating endometriosis (die), ovarian endometriosis, adhesions   
4          adhesions, ovarian cysts, de

## Ta sama procedura dla kolumny Wyodrebnione_dodatkowe_choroby_i_zaburzenia

In [42]:
# Ekstrakcja unikalnych wyrażeń dla kolumny Wyodrebnione_dodatkowe_choroby_i_zaburzenia, używam wcześniej utworzonej funkcji extract_unique_values
unique_diseases = extract_unique_values(df, "Wyodrebnione_dodatkowe_choroby_i_zaburzenia")

# Konwersja do listy
unique_diseases_list = unique_diseases.tolist()

In [43]:
# Szablony promptów zmodyfikowane w stosunku do wcześniejszych do celów grupowania wyrażeń związanych z chorobami
system_template = """
You are an assistant that helps group medical conditions into a single, concise, and representative term. For example:
- "Hypertension" and "High blood pressure" → "Hypertension"
- "Brain cysts" and "Cysts in the brain" → "Brain cysts"
- "Lung tumors" and "Lung cancer" → "Lung tumors"
- "Hypothyroidism" and "Thyroid underactivity" → "Hypothyroidism"
- "Chronic hepatitis" and "Liver inflammation" → "Chronic hepatitis"
- "Insulin resistance" and "Impaired insulin sensitivity" → "Insulin resistance"
- "Depression" and "Major depressive disorder" → "Depression"
- "reflux" → "reflux"
- "sibo" → "sibo"
- "chronic anxiety" and "anxiety neurosis" → "anxiety"

Provide only the most concise and representative term for the input medical condition. Do not include additional descriptions, punctuation, or explanations.
"""

# Zmieniony human_template, aby pozostał zgodny z system_template
human_template = """
What is the most representative term for the following medical condition: "{term}"?
"""

system_prompt = SystemMessagePromptTemplate.from_template(system_template)
human_prompt = HumanMessagePromptTemplate.from_template(human_template)
chat_template = ChatPromptTemplate.from_messages([system_prompt, human_prompt])

# Funkcje takie same jak dla symptomów, są wyżej

# Lista unikalnych diagnoz
unique_diseases = unique_diseases_list

# Generowanie słownika normalizacji
normalization_dict_diseases = create_normalization_dict(unique_diseases)

# Zamiana kluczy i wartości na małe litery
znormalizowane_dict_diseases = {key.lower(): value.lower() for key, value in normalization_dict_diseases.items()}


In [44]:
# Wyświetlenie wyniku
znormalizowane_dict_diseases

{'hypertension': 'hypertension',
 'brain cysts': 'brain cysts',
 'lung tumors': 'lung tumors',
 'hypothyroidism': 'hypothyroidism',
 'chronic hepatitis': 'chronic hepatitis',
 'insulin resistance': 'insulin resistance',
 'depression': 'depression',
 "hashimoto's disease": "hashimoto's thyroiditis",
 'goiters': 'goiter',
 'inflammation': 'inflammation',
 'hypothyroidism.': 'hypothyroidism',
 'pcos': 'polycystic ovary syndrome',
 'hemangioma': 'hemangioma',
 'reflux': 'reflux',
 'anxiety disorders': 'anxiety',
 'migraines': 'migraines',
 'sibo': 'sibo',
 'inflammation of tendon sheaths': 'tenosynovitis',
 'fibromyalgia': 'fibromyalgia',
 'parietal bone hemangioma': 'parietal bone hemangioma',
 'eosinophilic gastroenteritis': 'eosinophilic gastroenteritis',
 'left labyrinthine damage': 'labyrinthine damage',
 'hypotension': 'hypotension',
 'bilateral scoliosis.': 'scoliosis',
 'asthma': 'asthma',
 'latent tetany': 'tetany',
 'varicose veins': 'varicose veins',
 'thyroid nodules': 'thyroid

In [45]:
# Zastosowanie wcześniej utworzonej funkcji normalize_text_column do kolumny z diagnozami: "Wyodrebnione_dodatkowe_choroby_i_zaburzenia"
df["Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane"] = df["Wyodrebnione_dodatkowe_choroby_i_zaburzenia"].apply(normalize_text_column, args=(znormalizowane_dict_diseases,))

# Przeniesienie kolumn z wyestrahowanymi informacjami przed ich odpowiadającą kolumną
cols = list(df.columns)
cols.insert(cols.index('Tlumaczenie_Ang_Jakie_inne_choroby_entities'), cols.pop(cols.index('Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane')))

# Przestawienie DataFrame według zaktualizowanej listy kolumn:
df = df[cols]

# Usunięcie powtórzeń w komórkach kolumny "Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane"
# Zastosowanie wcześniej utworzonej funkcji (przy symptomach): remove_duplicate_phrases
df['Wyodrebnione_dodatkowe_choroby_i_zaburzenia_i_zaburzenia_znormalizowane'] = df['Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane'].apply(remove_duplicate_phrases)


In [46]:
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                               Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0      adhesions, adenomyosis, deep infiltrating endometriosis (die), cervical endometriosis, adnexal endometriosis   
1                                                                 abdominal pain, peritoneal disease, endometriosis   
2  advanced endometriosis, adhesions, ovarian endometriosis, rectal masses, ovarian adhesions, bladder displacement   
3                              adenomyosis, deep infiltrating endometriosis (die), ovarian endometriosis, adhesions   
4          adhesions, ovarian cysts, de

In [47]:
df.head(2)

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   

                                                                                                                                                                                    Wyodrebnione_rozpoznania_pooperacyjne  \
0  Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                  Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   

                                                           Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0  adhesions, adenomyosis, deep infiltrating endometriosis (die), cervical endometriosis, adnexal endometriosis   
1                                                             abdominal pain, peritoneal disease, endometriosis   

                                                                                                                                                                                                                                                                                                                                                               Tlumaczenie_Ang_Rozpoznanie_pooperacyjne  \
0  Condition after 4 surgical procedures. Intra-abdominal adhesions. Adenomyosis of the uterine body. Deep infiltrating endometriosis of the left parametrium. In the area of the left ureter and the left uterosacral ligament. Right parametric endometriosis. In the area of the right ureter and the right uterosacral ligament. Endometrial tumor at the cervix. Endometriosis of the left adnexa.   
1                                                                                                                                                                                                                                                                                                               Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis.   

                                                                                                                                              Wyodrebnione_zakres_operacji_znormalizowane  \
0                                                   adhesiolysis, excision of endometriosis from the bilateral parametrium, hysterectomy, adhesion prevention, peritoneal cavity drainage   
1  excision of peritoneal tissue, adhesiolysis, excision of the left sacrouterine ligament and peritoneum from the douglas pouch, excision of peritoneum from the anterior abdominal wall   

                                                                   Tlumaczenie_Ang_Zakres_operacji_entities  \
0                                [cervical tumor, peritoneal cavity, tumor, endometriosis, left, adhesions]   
1  [abdominal cavity, peritoneal tissues, left sacrouterine ligament, adhesions, anterior wall, peritoneum]   

                                                                                                                                                                                                         Wyodrebnione_zakres_operacji  \
0                                                               Release of adhesions, Removal of endometriosis from the left and right parametrium, Laparoscopic hysterectomy, Adhesion preventio

Zanim przejdę do kolejnego etapu, tym razem zamienię angielskie tłumaczenia na język polski, gdyż wynik ma być dla polskiego odbiorcy.

# LLM - podmiana języka angielskiego na polski

Wykorzystam ten sam kod, który był wykorzystany w części 1 projektu.

In [48]:
df.columns

Index(['Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities',
       'Wyodrebnione_rozpoznania_pooperacyjne',
       'Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane',
       'Tlumaczenie_Ang_Rozpoznanie_pooperacyjne',
       'Wyodrebnione_zakres_operacji_znormalizowane',
       'Tlumaczenie_Ang_Zakres_operacji_entities',
       'Wyodrebnione_zakres_operacji', 'Tlumaczenie_Ang_Zakres_operacji',
       'Czy_dolegliwosci', 'Tlumaczenie_Ang_Rodzaje_dolegliwosci_entities',
       'Wyodrebnione_dolegliwosci', 'Wyodrebnione_dolegliwosci_znormalizowane',
       'Tlumaczenie_Ang_Rodzaje_dolegliwosci', 'Rodzaj_operacji',
       'Czy_leczenie_hormonalne', 'Czy_dietetyk', 'Okres_dietetyk',
       'Czy_dieta_własna', 'Czy_Fizjoterapeuta_po_operacji',
       'Okres_fizjoterapeuta', 'Aktywnosc_fizyczna', 'Czy_inne_metody',
       'Wyodrebnione_dodatkowe_metody',
       'Wyodrebnione_dodatkowe_metody_znormalizowane',
       'Tlumaczenie_Ang_Jakie_inne_metody', 'Czy_warzywa_i_owoce_5_porcji',
     

In [49]:
def translate(description):
	#Tworzę dwa łańcuchy (chains):
    
    # 1. Wykrywanie języka
    template1 = "Return the language this description is written in:\n{description}.\nONLY return the language it was written in."
    prompt1 = ChatPromptTemplate.from_template(template1)
    chain_1 = prompt1|model_1
    
    # 2. Tłumaczenie z wykrytego języka na angielski
    template2 = "Translate the following medical description from {language} into Polish. Ensure that the translation is accurate and uses proper medical terminology. Please provide only the translated text without any additional explanations or statements. Here is the description:\n"+description
    prompt2 = ChatPromptTemplate.from_template(template2)
    chain_2 = prompt2|model_1

    language_chain = chain_1
    translation_chain = language_chain|chain_2
    
    return translation_chain.invoke(description)

In [50]:
# Funkcja do tłumaczenia i przetwarzania wyników
def translate_and_parse(description):
    if pd.isna(description):
        return np.nan  # Zwróć NaN, jeśli opis jest NaN
    result = translate(description)
    translate_result_content = result.content
    return translate_result_content

# Zastosowanie funkcji do każdego opisu w DataFrame
df['Tlumaczenie_PL_Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'] = df['Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'].apply(translate_and_parse)
df['Tlumaczenie_PL_Wyodrebnione_zakres_operacji_znormalizowane'] = df['Wyodrebnione_zakres_operacji_znormalizowane'].apply(translate_and_parse)
df['Tlumaczenie_PL_Wyodrebnione_dolegliwosci_znormalizowane'] = df['Wyodrebnione_dolegliwosci_znormalizowane'].apply(translate_and_parse)
df['Tlumaczenie_PL_Wyodrebnione_dodatkowe_metody_znormalizowane'] = df['Wyodrebnione_dodatkowe_metody_znormalizowane'].apply(translate_and_parse)
df['Tlumaczenie_PL_Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane'] = df['Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane'].apply(translate_and_parse)

In [53]:
#Nowe kolumny są na końcu dataframe. Przestawię je przed odpowiadającymi im kolumnami macierzystymi dla łatwiejszego czytania dataframu.

#Kolumny dataframe:
cols = list(df.columns)

cols.insert(cols.index('Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane'), cols.pop(cols.index('Tlumaczenie_PL_Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane')))

cols.insert(cols.index('Wyodrebnione_zakres_operacji_znormalizowane'), cols.pop(cols.index('Tlumaczenie_PL_Wyodrebnione_zakres_operacji_znormalizowane')))

cols.insert(cols.index('Wyodrebnione_dolegliwosci_znormalizowane'), cols.pop(cols.index('Tlumaczenie_PL_Wyodrebnione_dolegliwosci_znormalizowane')))

cols.insert(cols.index('Wyodrebnione_dodatkowe_metody_znormalizowane'), cols.pop(cols.index('Tlumaczenie_PL_Wyodrebnione_dodatkowe_metody_znormalizowane')))

cols.insert(cols.index('Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane'), cols.pop(cols.index('Tlumaczenie_PL_Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane')))

# Przestawienie DataFrame według zaktualizowanej listy kolumn:
data_transl = df[cols]
data_transl.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                               Tlumaczenie_PL_Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane  \
0               zrosty, gruczolistość, głęboko naciekająca endometrioza (DIE), endometrioza szyjki macicy, endometrioza przydatków   
1                                                                                     ból brzucha, choroba otrzewnej, endometrioza   
2  zaawansowana endometrioza, zrosty, endometrioza jajników, masy odbytnicze, zrosty jajnikowe, przemieszczenie pęcherza moczowego   
3                                               adenomioza, głęboko naciekająca endometrioza (DIE)

In [ ]:
# Zapis do pliku json
data_transl.to_json('C:/Users/justy/Documents/Projekt/04_projekt_znormalizowane_kolumny_z_opisami_od_ankietowanych.json', orient='records')

In [186]:
# Wczytanie danych
df = pd.read_json('C:\\Users\\justy\\Documents\\Projekt\\04_projekt_znormalizowane_kolumny_z_opisami_od_ankietowanych.json')

#(Kroki: zapis do pliku json i wczytanie danych wykonane po to, aby w razie problemów mieć gotową kopię przetłumaczonych danych i nie trzeba było przechodzić całego kodu od początku.)

Skrócę nazwy niektórych kolumn:

In [187]:
# Zmiana nazw kolumn
df = df.rename(columns={'Tlumaczenie_PL_Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane': 'rozpoznania_pooperacyjne', 
                        'Tlumaczenie_PL_Wyodrebnione_zakres_operacji_znormalizowane': 'zakres_operacji',
                        'Tlumaczenie_PL_Wyodrebnione_dolegliwosci_znormalizowane' : 'dolegliwości',
                        'Tlumaczenie_PL_Wyodrebnione_dodatkowe_metody_znormalizowane' : 'dodatkowe_metody',
                        'Tlumaczenie_PL_Wyodrebnione_dodatkowe_choroby_i_zaburzenia_znormalizowane' : 'dodatkowe_choroby_i_zaburzenia'})

df.head(5)

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             Intra-abdominal adhesions, Adenomyosis of the uterine body, Deep infiltrating endometriosis of the left parametrium, Right parametric endometriosis, Endometrial tumor at the cervix, Endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             Pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  Stage IV endometriosis, Adhesions, Frozen pelvis, Endometrial mass on the ovary, Masses in the rectum, Bowel fused with the uterus, Bowel adhered to the peritoneum, Ovaries retracted behind the uterus, Ovaries fused with the uterus, Ovaries fused with the bowel, Bladder displaced, Bladder tethered by adhesions, Adhesions on the parametrium, Adhesions on the ligaments   
3                                                                                                                                                                                                                                              Advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        Intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the Douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                                                                          rozpoznania_pooperacyjne  \
0               zrosty, gruczolistość, głęboko naciekająca endometrioza (DIE), endometrioza szyjki macicy, endometrioza przydatków   
1                                                                                     ból brzucha, choroba otrzewnej, endometrioza   
2  zaawansowana endometrioza, zrosty, endometrioza jajników, masy odbytnicze, zrosty jajnikowe, przemieszczenie pęcherza moczowego   
3                                               adenomioza, głęboko naciekająca endometrioza (DIE)

In [188]:
#Upewniam się jeszcze, że wszystkie teksty będą składały się tylko z małych liter aby ujednolicić teksty (Ból i ból byłyby traktowane jako dwa osobne symptomy)
def to_lowercase(x):
    if isinstance(x, str):
        return x.lower()
    elif isinstance(x, list):
        return [item.lower() if isinstance(item, str) else item for item in x]
    else:
        return x

df = df.applymap(to_lowercase)

In [189]:
df.head(5)

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             intra-abdominal adhesions, adenomyosis of the uterine body, deep infiltrating endometriosis of the left parametrium, right parametric endometriosis, endometrial tumor at the cervix, endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  stage iv endometriosis, adhesions, frozen pelvis, endometrial mass on the ovary, masses in the rectum, bowel fused with the uterus, bowel adhered to the peritoneum, ovaries retracted behind the uterus, ovaries fused with the uterus, ovaries fused with the bowel, bladder displaced, bladder tethered by adhesions, adhesions on the parametrium, adhesions on the ligaments   
3                                                                                                                                                                                                                                              advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                                                                          rozpoznania_pooperacyjne  \
0               zrosty, gruczolistość, głęboko naciekająca endometrioza (die), endometrioza szyjki macicy, endometrioza przydatków   
1                                                                                     ból brzucha, choroba otrzewnej, endometrioza   
2  zaawansowana endometrioza, zrosty, endometrioza jajników, masy odbytnicze, zrosty jajnikowe, przemieszczenie pęcherza moczowego   
3                                               adenomioza, głęboko naciekająca endometrioza (die)

Zauważyłam jeszcze, że endometrioza jajnikowa w rozpoznaniu pooperacyjnym jest nazywana w zróżnicowany sposób. Podobnie jest dla endometriozy jelitowej, zrostów, endometriozy (ogólnej).
Najprawdopodbniej jest to spowodowane niedoskonałościami tłumaczenia przez LLM, dodatkowo wyodrębnianie rozpoznań również nie przebiegło w idealny sposób.
Aby analiza była bardziej zbliżona do optymalnej, ujednolicę te nazwy.

In [ ]:
# Definicje mapowania nazw
mapping = {
    'endometrioza jajnika': ['endometrioza przydatków', 'endometrioza jajników', 'endometrioza jajnikowa', 'torbiel jajnika', 'guz jajnika', 'torbiele jajników'],
    'endometrioza jelitowa': ['endometrioza odbytnicy', 'masy odbytnicze', 'endometrioza jelitowa'],
    'endometrioza': ['endometrioza', 'gruczolistość'],
    'zaawansowana endometrioza': ['zaawansowana endometrioza', 'endometrioza stopnia iv'],
    'mięśniaki macicy': ['mięśniaki macicy', 'mięśniak macicy'],
    'adenomioza': ['endometrioza macicy', 'adenomioza']
}

def normalize_name(diagnosis_str):
    """Normalizuje diagnozy w pojedynczym stringu."""
    diagnoses = diagnosis_str.split(', ')  # Rozdzielamy string na listę diagnoz
    normalized = set()  # Używamy set, by uniknąć duplikatów
    
    for diagnosis in diagnoses:
        replaced = False
        for new_name, old_names in mapping.items():
            if diagnosis in old_names:
                normalized.add(new_name)
                replaced = True
                break
        if not replaced and 'zrosty' in diagnosis:
            normalized.add('zrosty')
        elif not replaced:
            normalized.add(diagnosis)

    return ', '.join(sorted(normalized))  # Łączymy wynik w string

# Zastosowanie na kolumnie DataFrame
df['rozpoznania_pooperacyjne'] = df['rozpoznania_pooperacyjne'].apply(normalize_name)




In [191]:
df.head()

Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities  \
0  [uterine body, left parametrium, adenomyosis of the uterine body, endometrial tumor, left adnexa, endometriosis, left uterosacral ligament, uterosacral ligament, ureter, cervix, intra-abdominal adhesions]   
1                                                                                                                                               [peritoneal, abdomen, endometriosis, peritoneal diseases, pain]   
2                                                                           [bladder, ligaments, parametrium, bowel, ovary, ovaries, rectum, uterus, endometriosis, adhesions, endometrial, masses, peritoneum]   
3                                                                                                      [adenomyosis, ovarian, intra-abdominal, endometriosis, ovarian endometriosis, intra-abdominal adhesions]   
4                                    [ovarian, extra-peritoneal adhesions,, uterosacral ligaments, right ovarian cysts, rectum, endometrial polyp, endometriosis, intestine, douglas pouch, endometrial tumors]   

                                                                                                                                                                                                                                                                                                                                               Wyodrebnione_rozpoznania_pooperacyjne  \
0                                                                                                                                                             intra-abdominal adhesions, adenomyosis of the uterine body, deep infiltrating endometriosis of the left parametrium, right parametric endometriosis, endometrial tumor at the cervix, endometriosis of the left adnexa   
1                                                                                                                                                                                                                                                                                             pain localized in other parts of the lower abdomen, peritoneal diseases, endometriosis   
2  stage iv endometriosis, adhesions, frozen pelvis, endometrial mass on the ovary, masses in the rectum, bowel fused with the uterus, bowel adhered to the peritoneum, ovaries retracted behind the uterus, ovaries fused with the uterus, ovaries fused with the bowel, bladder displaced, bladder tethered by adhesions, adhesions on the parametrium, adhesions on the ligaments   
3                                                                                                                                                                                                                                              advanced adenomyosis, left parametric endometriosis, right parametric endometriosis, ovarian endometriosis, intra-abdominal adhesions   
4                                                                                        intra- and extra-peritoneal adhesions, right ovarian cysts, deeply infiltrating endometriosis of the intestine, endometrial tumors on the rectum, deeply infiltrating endometriosis of the douglas pouch, endometrial polyp, deeply infiltrating endometriosis on the uterosacral ligaments   

                                                                                             rozpoznania_pooperacyjne  \
0      endometrioza, endometrioza jajnika, endometrioza szyjki macicy, głęboko naciekająca endometrioza (die), zrosty   
1                                                                        ból brzucha, choroba otrzewnej, endometrioza   
2  endometrioza jajnika, endometrioza jelitowa, przemieszczenie pęcherza moczowego, zaawansowana endometrioza, zrosty   
3                                    adenomioza, endometrioza jajnika, głęboko naciekająca endometrioza (die), zrosty   
4    endometrioza jajnika, en

# Analiza danych przy użycia Ydata_profiling

Po tym kroku dane już powinny nadawać się do dalszej analizy.
Przed analizą jeszcze usunę z dataframe df kolumny robocze i te, które służyły mi tylko jako odnośnik do sprawdzania czy poprawnie działa przetwarzanie tekstu.
Nie będę usuwać kolumny z nazwami NER, bo nie jestem pewna czy to nie one bedą odpowiedniejsze do dalszej analizy.

In [192]:
df.columns	#wyświetlam jakie mam kolumny

Index(['Tlumaczenie_Ang_Rozpoznanie_pooperacyjne_entities',
       'Wyodrebnione_rozpoznania_pooperacyjne', 'rozpoznania_pooperacyjne',
       'Wyodrebnione_rozpoznania_pooperacyjne_znormalizowane',
       'Tlumaczenie_Ang_Rozpoznanie_pooperacyjne', 'zakres_operacji',
       'Wyodrebnione_zakres_operacji_znormalizowane',
       'Tlumaczenie_Ang_Zakres_operacji_entities',
       'Wyodrebnione_zakres_operacji', 'Tlumaczenie_Ang_Zakres_operacji',
       'Czy_dolegliwosci', 'Tlumaczenie_Ang_Rodzaje_dolegliwosci_entities',
       'Wyodrebnione_dolegliwosci', 'dolegliwości',
       'Wyodrebnione_dolegliwosci_znormalizowane',
       'Tlumaczenie_Ang_Rodzaje_dolegliwosci', 'Rodzaj_operacji',
       'Czy_leczenie_hormonalne', 'Czy_dietetyk', 'Okres_dietetyk',
       'Czy_dieta_własna', 'Czy_Fizjoterapeuta_po_operacji',
       'Okres_fizjoterapeuta', 'Aktywnosc_fizyczna', 'Czy_inne_metody',
       'Wyodrebnione_dodatkowe_metody', 'dodatkowe_metody',
       'Wyodrebnione_dodatkowe_metody_znormali

In [193]:
# Lista nazw kolumn, które chcę wybrać
columns_to_new_df = ['rozpoznania_pooperacyjne', 'zakres_operacji', 'Czy_dolegliwosci', 'dolegliwości',
       'Rodzaj_operacji', 'Czy_leczenie_hormonalne',
       'Czy_dietetyk', 'Okres_dietetyk', 'Czy_dieta_własna',
       'Czy_Fizjoterapeuta_po_operacji', 'Okres_fizjoterapeuta',
       'Aktywnosc_fizyczna', 'Czy_inne_metody', 'dodatkowe_metody',
       'Czy_warzywa_i_owoce_5_porcji', 'Czy_inne_choroby',
       'dodatkowe_choroby_i_zaburzenia', 'Ile_operacji',
       'Czy_operacja_zwiadowcza', 'Ile_po_operacji',
       'Zdrowe_srodowisko (0 Nie, 1 Tak)', 'BMI_kategoria', 'Grupa_wiekowa']

# Tworzenie nowego DataFrame z wybranymi kolumnami
df_analysis = df[columns_to_new_df]


In [194]:
# Zapis do pliku json
df_analysis.to_json('C:/Users/justy/Documents/Projekt/04_projekt_znormalizowane_i_wybrane_kolumny_do_końcowej_analizy.json', orient='records')

In [3]:
# Wczytanie danych
df_analysis = pd.read_json('C:\\Users\\justy\\Documents\\Projekt\\04_projekt_znormalizowane_i_wybrane_kolumny_do_końcowej_analizy.json')

#(Kroki: zapis do pliku json i wczytanie danych wykonane po to, aby w razie problemów mieć gotową kopię przetłumaczonych danych i nie trzeba było przechodzić całego kodu od początku.)

In [3]:
df_analysis.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57 entries, 0 to 56
Data columns (total 23 columns):
 #   Column                            Non-Null Count  Dtype 
---  ------                            --------------  ----- 
 0   rozpoznania_pooperacyjne          57 non-null     object
 1   zakres_operacji                   57 non-null     object
 2   Czy_dolegliwosci                  57 non-null     object
 3   dolegliwości                      31 non-null     object
 4   Rodzaj_operacji                   57 non-null     object
 5   Czy_leczenie_hormonalne           57 non-null     object
 6   Czy_dietetyk                      57 non-null     object
 7   Okres_dietetyk                    23 non-null     object
 8   Czy_dieta_własna                  46 non-null     object
 9   Czy_Fizjoterapeuta_po_operacji    57 non-null     object
 10  Okres_fizjoterapeuta              29 non-null     object
 11  Aktywnosc_fizyczna                57 non-null     object
 12  Czy_inne_metody         

In [196]:
report = ProfileReport(df_analysis)
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Data_profiling nie pokazuje wizualizacji dla fraz, ale dla słów, co powoduje powstanie szumu (wyrazy typu the, of itp.). Dla kolumn opisowych lepszy wynik da wykonanie osobnych wykresów z chmurą wyrażeń, a nie słów.

W kolejnym kroku zrobię zestawienie interesujących mnie wizualizacji, przy czym będą to wizualizacje całych fraz a nie tylko słów.

# Wykresy chmurowe dla kolumn opisowych (z dolegliwościami, diagnozami itp.)

## Wykresy dla kolumny 'dolegliwości'

Najpierw zrobię wizualizację dla kolumny 'Wyodrebnione_dolegliwosci_znormalizowane' i sprawdzę czy wynik jest zadowalający.

In [4]:
# Rozwijam listy z kolumny 'dolegliwości' na pojedyncze wiersze
exploded_df = df_analysis.explode('dolegliwości')

# Zbieram wszystkie frazy do jednej listy
phrase_list_symptoms_nlp = exploded_df['dolegliwości'].dropna().astype(str).tolist()

# Zamieniam spacje w frazach na podkreślniki, aby były traktowane jako pojedyncze "słowa"
phrase_list_symptoms_nlp = [fraza.replace(' ', '_') for fraza in phrase_list_symptoms_nlp]

# Wyświetlam wynik
print(phrase_list_symptoms_nlp)

['ból_pleców,_problemy_z_oddawaniem_moczu,_zatrzymanie_moczu,_ból_moczowodowy,_ból_nerek', 'ostry_ból,_zimne_poty,_zaparcia', 'ból_brzucha_po_lewej_stronie,_ból_pleców', 'ból_brzucha', 'ból_brzucha_po_lewej_stronie,_ból_w_pachwinie,_ból_brzucha,_problemy_z_oddawaniem_moczu,_zatrzymanie_moczu', 'problemy_z_oddawaniem_moczu,_zatrzymanie_moczu', 'problemy_z_układem_moczowym,_ból_brzucha', 'zrosty,_ogólny_dyskomfort', 'brak_objawów_podanych', 'biegunka,_problemy_z_układem_moczowym,_ból_brzucha', '"dyskomfort_brzuszny"', 'rwa_kulszowa,_ból_pośladka', 'ból_miednicy,_mastalgia,_nadmierna_potliwość,_ból_brzucha,_ból_pleców', 'tkliwość_brzucha,_drętwienie_pochwy,_zaparcia', 'ból_jajników,_ból_nóg,_ból_brzucha,_"ból_żeber",_ból_w_klatce_piersiowej,_ból_ramienia', 'częstomocz,_ból_pęcherza,_ból_jajników,_objaw_oddechowy,_krwioplucie', 'dysuria,_tkliwość_brzucha,_zaparcia', 'ból_brzucha_po_lewej_stronie,_obrzęk', 'zmęczenie,_ból_brzucha_po_lewej_stronie,_ból_pleców', 'drętwienie,_przewlekły_ból,_b

In [5]:
# Usunięcie '_' na początku fraz
cleaned_list = [
    ','.join([phrase.lstrip('_') for phrase in item.split(',')])  # Rozbicie, usunięcie `_`, połączenie
    for item in phrase_list_symptoms_nlp
]

print(cleaned_list)


['ból_pleców,problemy_z_oddawaniem_moczu,zatrzymanie_moczu,ból_moczowodowy,ból_nerek', 'ostry_ból,zimne_poty,zaparcia', 'ból_brzucha_po_lewej_stronie,ból_pleców', 'ból_brzucha', 'ból_brzucha_po_lewej_stronie,ból_w_pachwinie,ból_brzucha,problemy_z_oddawaniem_moczu,zatrzymanie_moczu', 'problemy_z_oddawaniem_moczu,zatrzymanie_moczu', 'problemy_z_układem_moczowym,ból_brzucha', 'zrosty,ogólny_dyskomfort', 'brak_objawów_podanych', 'biegunka,problemy_z_układem_moczowym,ból_brzucha', '"dyskomfort_brzuszny"', 'rwa_kulszowa,ból_pośladka', 'ból_miednicy,mastalgia,nadmierna_potliwość,ból_brzucha,ból_pleców', 'tkliwość_brzucha,drętwienie_pochwy,zaparcia', 'ból_jajników,ból_nóg,ból_brzucha,"ból_żeber",ból_w_klatce_piersiowej,ból_ramienia', 'częstomocz,ból_pęcherza,ból_jajników,objaw_oddechowy,krwioplucie', 'dysuria,tkliwość_brzucha,zaparcia', 'ból_brzucha_po_lewej_stronie,obrzęk', 'zmęczenie,ból_brzucha_po_lewej_stronie,ból_pleców', 'drętwienie,przewlekły_ból,ból_nerwowy', 'problemy_żołądkowo-jelito

In [6]:
# Połączenie wszystkich fraz w jeden string
text = ','.join(cleaned_list)
text

'ból_pleców,problemy_z_oddawaniem_moczu,zatrzymanie_moczu,ból_moczowodowy,ból_nerek,ostry_ból,zimne_poty,zaparcia,ból_brzucha_po_lewej_stronie,ból_pleców,ból_brzucha,ból_brzucha_po_lewej_stronie,ból_w_pachwinie,ból_brzucha,problemy_z_oddawaniem_moczu,zatrzymanie_moczu,problemy_z_oddawaniem_moczu,zatrzymanie_moczu,problemy_z_układem_moczowym,ból_brzucha,zrosty,ogólny_dyskomfort,brak_objawów_podanych,biegunka,problemy_z_układem_moczowym,ból_brzucha,"dyskomfort_brzuszny",rwa_kulszowa,ból_pośladka,ból_miednicy,mastalgia,nadmierna_potliwość,ból_brzucha,ból_pleców,tkliwość_brzucha,drętwienie_pochwy,zaparcia,ból_jajników,ból_nóg,ból_brzucha,"ból_żeber",ból_w_klatce_piersiowej,ból_ramienia,częstomocz,ból_pęcherza,ból_jajników,objaw_oddechowy,krwioplucie,dysuria,tkliwość_brzucha,zaparcia,ból_brzucha_po_lewej_stronie,obrzęk,zmęczenie,ból_brzucha_po_lewej_stronie,ból_pleców,drętwienie,przewlekły_ból,ból_nerwowy,problemy_żołądkowo-jelitowe,zaparcia,ból_brzucha_po_lewej_stronie,zaburzenia_miesiączk

In [7]:
# Generowanie chmury wyrażeń
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(text)

# Wyświetlenie chmury wyrażeń
plt.figure(figsize=(10, 5))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')  # Ukrycie osi

# Dodanie tytułu
plt.title('Chmura wyrażeń związanych z dolegliwościami:', fontsize=16, pad=20)	#pad - odstęp między tytułem a wykresem

# Zapisanie wykresu do pliku (PNG)
plt.savefig('wykres_dolegliwości_chmura_wyrażeń.png', bbox_inches='tight')
plt.show()

In [8]:
# Zliczanie częstotliwości występowania fraz
phrase_counts = Counter(text.split(","))
print(phrase_counts)


Counter({'ból_brzucha': 9, 'ból_pleców': 8, 'zaparcia': 8, 'ból_brzucha_po_lewej_stronie': 6, 'zatrzymanie_moczu': 5, 'problemy_z_układem_moczowym': 4, 'problemy_z_oddawaniem_moczu': 3, 'częstomocz': 3, 'ból_w_pachwinie': 2, 'brak_objawów_podanych': 2, 'ból_miednicy': 2, 'tkliwość_brzucha': 2, 'ból_jajników': 2, 'ból_w_klatce_piersiowej': 2, 'ból_moczowodowy': 1, 'ból_nerek': 1, 'ostry_ból': 1, 'zimne_poty': 1, 'zrosty': 1, 'ogólny_dyskomfort': 1, 'biegunka': 1, '"dyskomfort_brzuszny"': 1, 'rwa_kulszowa': 1, 'ból_pośladka': 1, 'mastalgia': 1, 'nadmierna_potliwość': 1, 'drętwienie_pochwy': 1, 'ból_nóg': 1, '"ból_żeber"': 1, 'ból_ramienia': 1, 'ból_pęcherza': 1, 'objaw_oddechowy': 1, 'krwioplucie': 1, 'dysuria': 1, 'obrzęk': 1, 'zmęczenie': 1, 'drętwienie': 1, 'przewlekły_ból': 1, 'ból_nerwowy': 1, 'problemy_żołądkowo-jelitowe': 1, 'zaburzenia_miesiączkowania': 1, 'szybka_progresja_głęboko_naciekającej_endometriozy': 1, 'ból_neuropatyczny': 1, '"ból_jajników"': 1, 'dysmenorrhea': 1, 'prz

In [9]:
multiple_occurrences = sum(1 for count in phrase_counts.values() if count > 1)

print("Liczba fraz występujących więcej niż raz:", multiple_occurrences)

Liczba fraz występujących więcej niż raz: 14


In [12]:
# Wybranie 14 najczęściej występujących fraz
most_common_phrases = phrase_counts.most_common(14)	# wiele dolegliwości było podanych tylko 1 raz, ich nie będzie na wykresie

# Posortowanie fraz według częstotliwości w malejącej kolejności
most_common_phrases.sort(key=lambda x: x[1], reverse=False)

# Utworzenie dwóch list: frazy i ich częstotliwości
phrases, counts = zip(*most_common_phrases)

# Tworzenie wykresu słupkowego
fig = go.Figure(data=go.Bar(
    x=counts,  # Częstotliwości
    y=phrases,  # Frazy
    orientation='h',  # Poziome słupki
    marker=dict(
        color=counts,  # Kolorowanie słupków w zależności od częstotliwości
        colorscale='Tealrose',  # Skala kolorów Viridis
        colorbar=dict(title='Liczba wystąpień')  # Dodanie paska kolorów
    )
))

# Dodanie tytułu i etykiet
fig.update_layout(
    title='14 najczęściej występujących dolegliwości',
    xaxis_title='Liczba wystąpień',
    yaxis_title='Dolegliwości',
    xaxis=dict(tickmode='linear'),
    yaxis=dict(tickmode='linear'),
    template='plotly',  # Jasny motyw (biały obszar wykresu)
    showlegend=False
)

# Wyświetlenie wykresu
fig.show()


## Wykresy dla kolumny 'rozpoznania_pooperacyjne'

In [13]:
# Rozwijamy listy z kolumny 'rozpoznania_pooperacyjne' na pojedyncze wiersze
exploded_df = df_analysis.explode('rozpoznania_pooperacyjne')

# Zbieramy wszystkie frazy do jednej listy
phrase_list_diagnoses_nlp = exploded_df['rozpoznania_pooperacyjne'].dropna().astype(str).tolist()

# Zamieniamy spacje w frazach na podkreślniki, aby były traktowane jako pojedyncze "słowa"
phrase_list_diagnoses_nlp = [fraza.replace(' ', '_') for fraza in phrase_list_diagnoses_nlp]

# Usunięcie '_' na początku fraz
cleaned_list_diagnoses = [
    ','.join([phrase.lstrip('_') for phrase in item.split(',')])  # Rozbicie, usunięcie `_`, połączenie
    for item in phrase_list_diagnoses_nlp
]

# Połączenie wszystkich fraz w jeden string
text_diagnoses = ','.join(cleaned_list_diagnoses)
text_diagnoses

'endometrioza,endometrioza_jajnika,endometrioza_szyjki_macicy,głęboko_naciekająca_endometrioza_(die),zrosty,ból_brzucha,choroba_otrzewnej,endometrioza,endometrioza_jajnika,endometrioza_jelitowa,przemieszczenie_pęcherza_moczowego,zaawansowana_endometrioza,zrosty,adenomioza,endometrioza_jajnika,głęboko_naciekająca_endometrioza_(die),zrosty,endometrioza_jajnika,endometrioza_jelitowa,głęboko_naciekająca_endometrioza_(die),polip_endometrialny,zrosty,głęboko_naciekająca_endometrioza_(die),nowotwór_endometrialny,martwica_jajowodu,wodobrzusze,zapalenie_otrzewnej,zrosty,endometrioza_jajnika,adenomioza,endometrioza,endometrioza_otrzewnowa,uchyłek_pęcherza_moczowego,mięśniaki_macicy,torbiele,zaawansowana_endometrioza,zrosty,endometrioza,głęboko_naciekająca_endometrioza_(die),mięśniaki_macicy,rozrost_endometrium,zrosty,adenomioza,endometrioza,endometrioza_jelitowa,endometrioza_miednicy,głęboko_naciekająca_endometrioza_(die),adenomioza,zrosty,endometrioza_jajnika,zmiany_otrzewnowe,zrosty,ból_brzuch

In [14]:
# Generowanie chmury wyrażeń
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(text_diagnoses)

# Wyświetlenie chmury wyrażeń
plt.figure(figsize=(10, 5))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')  # Ukrycie osi

# Dodanie tytułu
plt.title('Chmura wyrażeń związanych \nz diagnozami pooperacyjnymi:', fontsize=16)

# Zapisanie wykresu do pliku (PNG)
plt.savefig('wykres_diagnozy_chmura_wyrażeń.png', bbox_inches='tight')
plt.show()

In [15]:
# Zliczanie częstotliwości występowania fraz
phrase_diagnoses_counts = Counter(text_diagnoses.split(","))
phrase_diagnoses_counts

Counter({'endometrioza': 16,
         'endometrioza_jajnika': 28,
         'endometrioza_szyjki_macicy': 3,
         'głęboko_naciekająca_endometrioza_(die)': 19,
         'zrosty': 28,
         'ból_brzucha': 2,
         'choroba_otrzewnej': 1,
         'endometrioza_jelitowa': 8,
         'przemieszczenie_pęcherza_moczowego': 1,
         'zaawansowana_endometrioza': 7,
         'adenomioza': 15,
         'polip_endometrialny': 1,
         'nowotwór_endometrialny': 1,
         'martwica_jajowodu': 1,
         'wodobrzusze': 1,
         'zapalenie_otrzewnej': 1,
         'endometrioza_otrzewnowa': 4,
         'uchyłek_pęcherza_moczowego': 1,
         'mięśniaki_macicy': 5,
         'torbiele': 1,
         'rozrost_endometrium': 3,
         'endometrioza_miednicy': 1,
         'zmiany_otrzewnowe': 1,
         'ból_jajników': 1,
         'ból_pleców': 1,
         'niedrożność_jelit_z_zapaleniem': 1,
         'polip_macicy': 1,
         'zmiany_zapalne_w_jamie_brzusznej_i_kości_krzyżowej'

In [16]:
multiple_occurrences = sum(1 for count in phrase_diagnoses_counts.values() if count > 1)

print("Liczba fraz występujących więcej niż raz:", multiple_occurrences)

Liczba fraz występujących więcej niż raz: 14


In [17]:
# Wybranie 14 najczęściej występujących fraz
most_common_diagnoses_phrases = phrase_diagnoses_counts.most_common(multiple_occurrences)

# Posortowanie fraz według częstotliwości w malejącej kolejności
most_common_diagnoses_phrases.sort(key=lambda x: x[1], reverse=False)

# Utworzenie dwóch list: frazy i ich częstotliwości
phrases, counts = zip(*most_common_diagnoses_phrases)

# Tworzenie wykresu słupkowego
fig = go.Figure(data=go.Bar(
    x=counts,  # Częstotliwości
    y=phrases,  # Frazy
    orientation='h',  # Poziome słupki
    marker=dict(
        color=counts,  # Kolorowanie słupków w zależności od częstotliwości
        colorscale='Tealrose',  # Skala kolorów Viridis
        colorbar=dict(title='Liczba wystąpień')  # Dodanie paska kolorów
    )
))

# Dodanie tytułu i etykiet
fig.update_layout(
    title='Frazy związane z diagnozami pooperacyjnymi występujące więcej niż raz',
    xaxis_title='Liczba wystąpień',
    yaxis_title='Frazy',
    xaxis=dict(tickmode='linear'),
    yaxis=dict(tickmode='linear'),
    template='plotly',  # Jasny motyw (biały obszar wykresu)
    showlegend=False
)

# Wyświetlenie wykresu
fig.show()

## Wykresy dla kolumny 'zakres_operacji'

In [18]:
# Rozwijamy listy z kolumny 'zakres_operacji' na pojedyncze wiersze
exploded_df = df_analysis.explode('zakres_operacji')

# Zbieramy wszystkie frazy do jednej listy
phrase_list_surgery_nlp = exploded_df['zakres_operacji'].dropna().astype(str).tolist()

# Zamieniamy spacje w frazach na podkreślniki, aby były traktowane jako pojedyncze "słowa"
phrase_list_surgery_nlp = [fraza.replace(' ', '_') for fraza in phrase_list_surgery_nlp]

# Usunięcie '_' na początku fraz
cleaned_list_surgery = [
    ','.join([phrase.lstrip('_') for phrase in item.split(',')])  # Rozbicie, usunięcie `_`, połączenie
    for item in phrase_list_surgery_nlp
]

# Połączenie wszystkich fraz w jeden string
text_surgery = ','.join(cleaned_list_surgery)
text_surgery

'adhezioliza,wycięcie_endometriozy_z_obustronnego_parametrium,histerektomia,zapobieganie_zrostom,drenaż_jamy_otrzewnej,wycięcie_tkanki_otrzewnej,adhezyoliza,wycięcie_lewego_więzadła_krzyżowo-macicznego_i_otrzewnej_z_zatoki_douglasa,wycięcie_otrzewnej_z_przedniej_ściany_jamy_brzusznej,adhezioliza,salpingo-ooforektomia_po_lewej_stronie,wycięcie_endometriozy_z_prawego_jajnika,salpingo-ooforektomia_po_prawej_stronie,przezodbytnicza_resekcja_dysku_odbytnicy,histerektomia,trachelektomia,adhezioliza_i_repozycja_pęcherza_moczowego,adhezioliza,histerektomia,wycięcie_endometriozy_z_jajników_i_przydatków,zapobieganie_zrostom,drenaż_otrzewnowy,adhezioliza,wycięcie_torbieli_prawego_jajnika,resekcja_segmentalna_odbytnicy,wycięcie_głęboko_naciekającej_endometriozy_z_jelita,operacja_zatoki_douglasa,wycięcie_więzadeł_krzyżowo-macicznych,laparoskopia_diagnostyczna,wycięcie_zmian_endometrialnych,ooforektomia,salpingektomia,płukanie_jamy_brzusznej,adhezioliza,wycięcie_jednostronnego_guza_jajnika,wycięcie_

In [19]:
# Generowanie chmury wyrażeń
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(text_surgery)

# Wyświetlenie chmury wyrażeń
plt.figure(figsize=(10, 5))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')  # Ukrycie osi

# Dodanie tytułu
plt.title('Chmura wyrażeń związanych z wykonanymi \nprocedurami medycznymi podczas operacji:', fontsize=16)

# Zapisanie wykresu do pliku (PNG)
plt.savefig('wykres_operacje_co_zrobiono_chmura_wyrażeń.png', bbox_inches='tight')
plt.show()

In [20]:
# Zliczanie częstotliwości występowania fraz
phrase_surgery_counts = Counter(text_surgery.split(","))

In [21]:
multiple_occurrences = sum(1 for count in phrase_surgery_counts.values() if count > 1)

print("Liczba fraz występujących więcej niż raz:", multiple_occurrences)

Liczba fraz występujących więcej niż raz: 20


In [22]:
# Wybranie 20 najczęściej występujących fraz
most_common_surgery_phrases = phrase_surgery_counts.most_common(multiple_occurrences)

# Posortowanie fraz według częstotliwości w malejącej kolejności
most_common_surgery_phrases.sort(key=lambda x: x[1], reverse=False)

# Utworzenie dwóch list: frazy i ich częstotliwości
phrases, counts = zip(*most_common_surgery_phrases)

# Tworzenie wykresu słupkowego
fig = go.Figure(data=go.Bar(
    x=counts,  # Częstotliwości
    y=phrases,  # Frazy
    orientation='h',  # Poziome słupki
    marker=dict(
        color=counts,  # Kolorowanie słupków w zależności od częstotliwości
        colorscale='Tealrose',  # Skala kolorów Viridis
        colorbar=dict(title='Liczba wystąpień')  # Dodanie paska kolorów
    )
))

# Dodanie tytułu i etykiet
fig.update_layout(
    title='Frazy związane z wykonanymi procedurami medycznymi podczas operacji występujące więcej niż raz',
    xaxis_title='Liczba wystąpień',
    yaxis_title='Frazy',
    xaxis=dict(tickmode='linear'),
    yaxis=dict(tickmode='linear'),
    template='plotly',  # Jasny motyw (biały obszar wykresu)
    showlegend=False
)

# Wyświetlenie wykresu
fig.show()

## Wykresy dla kolumny 'dodatkowe_metody'

In [23]:
# Rozwijamy listy z kolumny 'Wyodrebnione_dodatkowe_metody_znormalizowane' na pojedyncze wiersze
exploded_df = df_analysis.explode('dodatkowe_metody')

# Zbieramy wszystkie frazy do jednej listy
phrase_list_additional_methods_nlp = exploded_df['dodatkowe_metody'].dropna().astype(str).tolist()

# Zamieniamy spacje w frazach na podkreślniki, aby były traktowane jako pojedyncze "słowa"
phrase_list_additional_methods_nlp = [fraza.replace(' ', '_') for fraza in phrase_list_additional_methods_nlp]

# Usunięcie '_' na początku fraz
cleaned_list_additional_methods = [
    ','.join([phrase.lstrip('_') for phrase in item.split(',')])  # Rozbicie, usunięcie `_`, połączenie
    for item in phrase_list_additional_methods_nlp
]

# Połączenie wszystkich fraz w jeden string
text_additional_methods = ','.join(cleaned_list_additional_methods)
text_additional_methods

'psychoterapia,akupunktura,joga,fizjoterapia,terapia_konopna,medytacja,terapia_masażem,akupunktura,naturoterapia,suplementy,medytacja,książki_samopomocowe,gimnastyka_słowiańska,medytacja,joga,medytacja,joga,psychoterapia,medytacja,joga,rozciąganie,terapia_masażem,fizjoterapia,joga,ćwiczenia,medytacja,antydepresanty,psychoterapia,spacery,terapia_snu,asmr,terapia_konopiami,zarządzanie_dietą,poradnictwo_dietetyczne,poradnictwo_żywieniowe,porady_petera_attii,ćwiczenia_kegla,medytacja,psychoterapia,medytacja,terapia_naturą,muzykoterapia,joga,medytacja,samoopieka,fizjoterapia,zarządzanie_dietą,unikanie_alergenów,aktywność_fizyczna,odpoczynek,neurologia,medytacja,fizjoterapia,medytacja,psychoterapia,medytacja,medytacja,psychoterapia,tradycyjna_medycyna_chińska,medytacja,psychoterapia,akupunktura,psychoterapia,medytacja,relaksacja,psychoterapia,medytacja,psychoterapia,akupunktura,medytacja,fizjoterapia,osteopatia,joga,techniki_relaksacyjne,medytacja,psychoterapia'

In [24]:
# Generowanie chmury wyrażeń
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(text_additional_methods)

# Wyświetlenie chmury wyrażeń
plt.figure(figsize=(10, 5))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')  # Ukrycie osi

# Dodanie tytułu
plt.title('Chmura wyrażeń związanych z dodatkowymi \nmetodami wspomagania organizmu:', fontsize=16)

# Zapisanie wykresu do pliku (PNG)
plt.savefig('wykres_dodatkowe_metody_chmura_wyrażeń.png', bbox_inches='tight')
plt.show()

In [25]:
# Zliczanie częstotliwości występowania fraz
phrase_additional_methods_counts = Counter(text_additional_methods.split(","))

In [26]:
multiple_occurrences = sum(1 for count in phrase_additional_methods_counts.values() if count > 1)

print("Liczba fraz występujących więcej niż raz:", multiple_occurrences)

Liczba fraz występujących więcej niż raz: 7


In [27]:
# Wybranie 7 najczęściej występujących fraz
most_common_additional_methods_phrases = phrase_additional_methods_counts.most_common(multiple_occurrences)

# Posortowanie fraz według częstotliwości w malejącej kolejności
most_common_additional_methods_phrases.sort(key=lambda x: x[1], reverse=False)

# Utworzenie dwóch list: frazy i ich częstotliwości
phrases, counts = zip(*most_common_additional_methods_phrases)

# Tworzenie wykresu słupkowego
fig = go.Figure(data=go.Bar(
    x=counts,  # Częstotliwości
    y=phrases,  # Frazy
    orientation='h',  # Poziome słupki
    marker=dict(
        color=counts,  # Kolorowanie słupków w zależności od częstotliwości
        colorscale='Tealrose',  # Skala kolorów Viridis
        colorbar=dict(title='Liczba wystąpień')  # Dodanie paska kolorów
    )
))

# Dodanie tytułu i etykiet
fig.update_layout(
    title='Frazy związane z dodatkowymi metodami wspomagania organizmu występujące więcej niż raz',
    xaxis_title='Liczba wystąpień',
    yaxis_title='Frazy',
    xaxis=dict(tickmode='linear'),
    yaxis=dict(tickmode='linear'),
    template='plotly',  # Jasny motyw (biały obszar wykresu)
    showlegend=False
)

# Wyświetlenie wykresu
fig.show()

## Wykresy dla kolumny 'dodatkowe_choroby_i_zaburzenia'

In [28]:
# Rozwijamy listy z kolumny 'dodatkowe_choroby_i_zaburzenia' na pojedyncze wiersze
exploded_df = df_analysis.explode('dodatkowe_choroby_i_zaburzenia')

# Zbieramy wszystkie frazy do jednej listy
phrase_list_additional_diseases_nlp = exploded_df['dodatkowe_choroby_i_zaburzenia'].dropna().astype(str).tolist()

# Zamieniamy spacje w frazach na podkreślniki, aby były traktowane jako pojedyncze "słowa"
phrase_list_additional_diseases_nlp = [fraza.replace(' ', '_') for fraza in phrase_list_additional_diseases_nlp]

# Usunięcie '_' na początku fraz
cleaned_list_additional_diseases = [
    ','.join([phrase.lstrip('_') for phrase in item.split(',')])  # Rozbicie, usunięcie `_`, połączenie
    for item in phrase_list_additional_diseases_nlp
]

# Połączenie wszystkich fraz w jeden string
text_additional_diseases = ','.join(cleaned_list_additional_diseases)
text_additional_diseases

'nadciśnienie,torbiele_mózgu,guzy_płuc,niedoczynność_tarczycy,przewlekłe_zapalenie_wątroby,insulinooporność,depresja,nadciśnienie,insulinooporność,depresja,nadciśnienie,niedoczynność_tarczycy,zapalenie_tarczycy_hashimoto,wole,zapalenie,niedoczynność_tarczycy,zespół_policystycznych_jajników,insulinooporność,niedoczynność_tarczycy,insulinooporność,naczyniak,refluks,insulinooporność,depresja,lęk,depresja,depresja,depresja,insulinooporność,choroba_hashimoto,depresja,migreny,sibo,niedoczynność_tarczycy,zapalenie_pochewki_ścięgnistej,fibromialgia,sibo,naczyniak_kości_ciemieniowej,eozynofilowe_zapalenie_żołądka_i_jelit,uszkodzenie_błędnika,hipotensja,skolioza,zapalenie_tarczycy_hashimoto,astma,tężyczka,zapalenie_tarczycy_hashimoto,insulinooporność,żylaki,guzki_tarczycy,utrata_słuchu,astma,niedoczynność_tarczycy,insulinooporność,lęk,sibo,h._pylori,astma,niedoczynność_tarczycy,zespół_jelita_drażliwego,przewlekłe_zapalenie_trzustki,nietolerancja_fodmap,alergie,insulinooporność,choroba_hashimoto,

In [29]:
# Generowanie chmury wyrażeń
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(text_additional_diseases)

# Wyświetlenie chmury wyrażeń
plt.figure(figsize=(10, 5))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')  # Ukrycie osi

# Dodanie tytułu
plt.title('Chmura wyrażeń związanych \nz dodatkowymi schorzeniami:', fontsize=16)

# Zapisanie wykresu do pliku (PNG)
plt.savefig('wykres_dodatkowe_choroby_chmura_wyrażeń.png', bbox_inches='tight')
plt.show()

In [30]:
# Zliczanie częstotliwości występowania fraz
phrase_additional_diseases_counts = Counter(text_additional_diseases.split(","))

In [31]:
multiple_occurrences = sum(1 for count in phrase_additional_diseases_counts.values() if count > 1)

print("Liczba fraz występujących więcej niż raz:", multiple_occurrences)

Liczba fraz występujących więcej niż raz: 12


In [32]:
# Wybranie 12 najczęściej występujących fraz
most_common_additional_diseases_phrases = phrase_additional_diseases_counts.most_common(multiple_occurrences)

# Posortowanie fraz według częstotliwości w malejącej kolejności
most_common_additional_diseases_phrases.sort(key=lambda x: x[1], reverse=False)

# Utworzenie dwóch list: frazy i ich częstotliwości
phrases, counts = zip(*most_common_additional_diseases_phrases)

# Tworzenie wykresu słupkowego
fig = go.Figure(data=go.Bar(
    x=counts,  # Częstotliwości
    y=phrases,  # Frazy
    orientation='h',  # Poziome słupki
    marker=dict(
        color=counts,  # Kolorowanie słupków w zależności od częstotliwości
        colorscale='Tealrose',  # Skala kolorów Viridis
        colorbar=dict(title='Liczba wystąpień')  # Dodanie paska kolorów
    )
))

# Dodanie tytułu i etykiet
fig.update_layout(
    title='Frazy związane z dodatkowymi schorzeniami występujące więcej niż raz',
    xaxis_title='Liczba wystąpień',
    yaxis_title='Frazy',
    xaxis=dict(tickmode='linear'),
    yaxis=dict(tickmode='linear'),
    template='plotly',  # Jasny motyw (biały obszar wykresu)
    showlegend=False
)

# Wyświetlenie wykresu
fig.show()

Na powyższych wykres widać liczbę występowania wyrażeń związanych z dolegliwościami, dodakowymi schorzeniami, procedurami operacyjnymi, diagnozami i dodatkowymi metodami wspomagania organizmu w chorobie.

Najczęśćiej występujące dolegliwości: ból brzucha, zaparcia, ból pleców i problemy z układem moczowym.
Najczęściej występujące rozpoznania pooperacyjne: zrosty, endometrioza jajników, endometrioza głęboko naciekająca, adenomioza.
Najczęściej wykonywane procedury medyczne: uwolnienie zrostów, histerektomia, zapobieganie zrostom, wycięcie endometriozy.
Najczęstrze metody wspomagania siebie: medytacja, psychoteriapia, joga.
Najczęściej występujące dodatkowe dolegliwości i schorzenia to: depresja, insulinooporność, niedoczynność tarczycy.


Na 57 ankiet większość osób (54,4%) odpowiedziało, że ma dolegliwości po operacjach, które nie występowały przed operacją, natomiast 45,6% odpowiedziało, że nie ma żadnych dolegliwości.

In [65]:
# Wykres kołowy dla kolumny "Czy_dolegliwosci"

# Zliczenie wartości w kolumnie Czy_dolegliwosci
value_counts = df['Czy_dolegliwosci'].value_counts()

colors = ['#FF0000', '#008000']  # Czerwony i zielony
if value_counts.iloc[0] < value_counts.iloc[1]:  # Jeśli druga wartość większa, zamiana kolorów
    colors.reverse()

# Tworzenie wykresu kołowego
fig = go.Figure(data=[go.Pie(
    labels=value_counts.index,  # 'tak' i 'nie'
    values=value_counts.values,  # Liczba wystąpień
    textinfo='percent+label',  # Wyświetlanie etykiet i procentów
    marker=dict(colors=colors)  # Dynamiczne kolory
)])

# Dodanie tytułu
fig.update_layout(title_text="Odpowiedzi w kolumnie 'Czy_dolegliwosci'", title_x=0.5)

# Wyświetlenie wykresu
fig.show()

